<h1 style="color:red;"> Capstone Project: Battle of Neighborhoods</h1>

### Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">
<ol>
    <li><a href="#1.-Introduction---Business-Problem">Introduction - Business Problem</a>        
    <li><a href="#2.Data">Data</a>        
    <li><a href="#3.-Methodology">Methodology</a>
</ol>
</div>

<h2 style="color:blue;">1. <u>Introduction - Business Problem</u> </h2>
<h3>Opening a Yoga Studio</h3>

<i>I want to open a new Yoga Studio in Toronto. Where should I open it? </i>
This is one of the questions that an entrepreneur would need to answer before starting his or her business. Location is key for a new business and one that requires careful research. In this capstone project, I will attempt to solve this problem through data analysis

<h2 style="color:blue;">2.<u>Data</u></h2>

To solve the problem, we will need data from various sources: 
<ul>
    <li><b>Foursquare</b>: we will be leveraging the existing venues for each neighborhood in order to analyze how many yoga studios are in each neighborhood. This will be used to assess the competition in each neighborhood</li>
    <li><b>Demographics</b>: age and sex. Since yoga studios tend to be popular among women, we will be taking this into consideration in our analysis. We will be looking at the number of female population for each neighborhood. This data will be retrieved from the Open Data section on the website of the City of Toronto. </li>
    <li><b>Average income per neighborhood</b>: It's important to know the purchasing power of the residents of each neighborhood before establishing a business. This will also be retrieved from the City of Toronto website.</li?
    
</ul>
Contains information licensed under the Open Government Licence – Toronto. Link: https://open.toronto.ca/open-data-license/

### Neighborhood Data Profile
In this section we will be building the Neighborhood data profile which is composed of Demographics (Age, sex), number of population in each neighborhood and the average income. 

#### Data Cleaning and Wrangling

In [1]:
import pandas as pd
import numpy as np
import wget
import requests
import csv
import geocoder
import geopy
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium
import json 
print("Libraries imported")

Libraries imported


### Getting the geolocation data

We will use the data from the previous assignment to retrieve the zip codes and then the geolocation data for each neighborhood. We will not use Borough in this section

In [24]:
#let's open the csv file
csvfile = "C:/Users/nirin/Downloads/output.csv"
neighpostal = pd.read_csv(csvfile,
                 header=0,
                 delimiter='  ',                 
                 quotechar='"',
                 error_bad_lines=False,
                 engine='python')
neighpostal.shape

(180, 3)

In [25]:
neighpostal.drop(neighpostal[neighpostal['Borough'] =='Not assigned'].index, inplace = True)
print("removed rows with Not assigned Borough")

removed rows with Not assigned Borough


In [26]:
neighpostal.shape

(103, 3)

In [27]:
neighpostal.tail(5)

Postal Code           Borough  \
160         M8X         Etobicoke   
165         M4Y  Downtown Toronto   
168         M7Y      East Toronto   
169         M8Y         Etobicoke   
178         M8Z         Etobicoke   

                                         Neighbourhood  
160  The Kingsway,Montgomery Road,Old Mill North,Ki...  
165                               Church and Wellesley  
168  Business reply mail Processing Centre,South Ce...  
169  Old Mill South,King's Mill Park,Sunnylea,Humbe...  
178  Mimico NW,The Queensway West,South of Bloor,Ki...

In [28]:
#Importing the geographical data
geodf = pd.read_csv("C:/Users/nirin/Geospatial_Coordinates.csv",                   
                 header=0,
                 delimiter=",",                 
                 error_bad_lines=False,
                 engine='python'
                   )
geodf.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [29]:
dfmerge = neighpostal.merge(geodf)
dfmerge.tail(5)

Postal Code           Borough  \
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  
98   The Kingsway,Montgomery Road,Old Mill North,Ki...  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100  Business reply mail Processing Centre,South Ce...  43.662744 -79.321558  
101  Old Mill South,King's Mill Park,Sunnylea,Humbe...  43.636258 -79.498509  
102  Mimico NW,The Queensway West,South of Bloor,Ki...  43.628841 -79.520999

In [30]:
dfmerge.rename(columns = {'Neighbourhood' : 'Neighborhood' }, inplace = True)

In [31]:
dfmerge.head()

Postal Code           Borough  \
0         M3A        North York   
1         M4A        North York   
2         M5A  Downtown Toronto   
3         M6A        North York   
4         M7A  Downtown Toronto   

                                        Neighborhood   Latitude  Longitude  
0                        Parkwoods,Parkwoods-Donalda  43.753259 -79.329656  
1                                   Victoria Village  43.725882 -79.315572  
2  Regent Park,Harbourfront,Moss Park,Mount Pleas...  43.654260 -79.360636  
3                    Lawrence Manor,Lawrence Heights  43.718518 -79.464763  
4         Queen's Park,Ontario Provincial Government  43.662301 -79.389494

In [32]:
dfmerge['Neighborhood'] = dfmerge['Neighborhood'].str.split(',')

In [33]:
dfmerge = dfmerge.explode('Neighborhood')
dfmerge.shape

(304, 5)

In [34]:
#Mini dataframe for testing API to limit calls
dfmerge2 = dfmerge[dfmerge['Neighborhood'].isin(["Yonge-Eglinton","Annex","Alderwood","Bendale","Briar Hill-Belgravia"])]
dfmerge2.shape

(5, 5)

Let's combine the demographics data with the geographical data

In [35]:
activePop.shape

(140, 3)

In [36]:
activePopGeo = activePop.merge(dfmerge)
activePopGeo.shape

(138, 7)

In [88]:
activePopGeo.head()

Neighborhood  Active Male  Active Female Postal Code  \
0               Agincourt North     0.004414       0.004773         M1V   
1  Agincourt South-Malvern West     0.004125       0.004199         M1B   
2                     Alderwood     0.001990       0.001979         M8W   
3                         Annex     0.005932       0.006451         M5R   
4             Banbury-Don Mills     0.003917       0.004356         M3B   

           Borough   Latitude  Longitude  
0      Scarborough  43.815252 -79.284577  
1      Scarborough  43.806686 -79.194353  
2        Etobicoke  43.602414 -79.543484  
3  Central Toronto  43.672710 -79.405678  
4       North York  43.745906 -79.352188

## Using Foursquare API

In this section, let's use the Foursquare API to get a list of the yoga studios around toronto for each neighborhood

In [38]:
import random # library for random number generation
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

In [39]:
CLIENT_ID = 'NGBR4FWG0IAT0DHXIBKYXI2E1JI2LEJMEL3L1YA1RW4CSLXG'
CLIENT_SECRET = '23BDE00ECXWL0IEIDFLXDMQIK0PERQTG1MSKSKUOGBPAQSRJ' 
VERSION = '20180323'
#VERSION = '20190425'
LIMIT = 20
print('My credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

My credentials:
CLIENT_ID: NGBR4FWG0IAT0DHXIBKYXI2E1JI2LEJMEL3L1YA1RW4CSLXG
CLIENT_SECRET:23BDE00ECXWL0IEIDFLXDMQIK0PERQTG1MSKSKUOGBPAQSRJ


In [106]:
query = 'yoga class'
radius = 500
neighb = 'Annex'
geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(neighb)
latitude = location.latitude
longitude = location.longitude
print(latitude, longitude)

43.6703377 -79.407117


In [41]:
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&v={}&ll={},{}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, latitude, longitude, query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=NGBR4FWG0IAT0DHXIBKYXI2E1JI2LEJMEL3L1YA1RW4CSLXG&client_secret=23BDE00ECXWL0IEIDFLXDMQIK0PERQTG1MSKSKUOGBPAQSRJ&v=20180323&ll=43.6703377,-79.407117&query=Yoga&radius=500&limit=20'

In [42]:
results = requests.get(url).json()
print(results['response'].keys())
results['response']['venues'][:100]

dict_keys(['venues'])


[{'id': '4d8631e140a7a35d05fe2fbe',
  'name': 'Yoga Flow',
  'contact': {},
  'location': {'address': '408 Dupont',
   'lat': 43.6738436345442,
   'lng': -79.41013364162487,
   'labeledLatLngs': [{'label': 'display',
     'lat': 43.6738436345442,
     'lng': -79.41013364162487}],
   'distance': 459,
   'postalCode': 'M5R 1X2',
   'cc': 'CA',
   'city': 'Toronto',
   'state': 'ON',
   'country': 'Canada',
   'formattedAddress': ['408 Dupont', 'Toronto ON M5R 1X2', 'Canada']},
  'categories': [],
  'verified': False,
  'stats': {'tipCount': 0,
   'usersCount': 0,
   'checkinsCount': 0,
   'visitsCount': 0},
  'beenHere': {'count': 0,
   'lastCheckinExpiredAt': 0,
   'marked': False,
   'unconfirmedCount': 0},
  'hereNow': {'count': 0, 'summary': 'Nobody here', 'groups': []},
  'referralId': 'v-1605368071',
  'venueChains': [],
  'hasPerk': False},
 {'id': '5172971c582f605c9fd91d82',
  'name': 'The Yoga Back Clinic',
  'contact': {},
  'location': {'address': 'Suite 100',
   'crossStreet'

In [48]:
venues = results['response']['venues']
    
nearby_venues = pd.json_normalize(venues) # flatten JSON
nearby_venues.tail()

id                        name  \
1  5172971c582f605c9fd91d82        The Yoga Back Clinic   
2  5467e4db498ef31d10e8fe9c  Yoga Heritage Healing Arts   
3  4b6a386af964a520c0cd2be3            Kula Yoga Studio   
4  4ccf654048b8370468d2ebde             Urban Edge Yoga   
5  4b368125f964a520f43625e3          Hot Yoga Challenge   

                                          categories  verified    referralId  \
1  [{'id': '4bf58dd8d48988d104941735', 'name': 'M...      True  v-1605368071   
2  [{'id': '4bf58dd8d48988d102941735', 'name': 'Y...     False  v-1605368071   
3  [{'id': '4bf58dd8d48988d102941735', 'name': 'Y...      True  v-1605368071   
4  [{'id': '4bf58dd8d48988d102941735', 'name': 'Y...     False  v-1605368071   
5  [{'id': '4bf58dd8d48988d102941735', 'name': 'Y...     False  v-1605368071   

  venueChains  hasPerk       location.address  location.lat  location.lng  \
1          []    False              Suite 100     43.674701    -79.408514   
2          []    False        982 Bathurst St     43.668750    -79.413173   
3          []    False      304 Brunswick Ave     43.665820    -79.407541   
4          []    False  324 bloor st west, #1     43.667145    -79.403595   
5          []    False    306-720 Spadina Ave     43.665413    -79.403298   

   ... stats.visitsCount  beenHere.count beenHere.lastCheckinExpiredAt  \
1  ...                 0               0                             0   
2  ...                 0               0                             0   
3  ...                 0               0                             0   
4  ...                 0               0                             0   
5  ...                 0               0                             0   

  beenHere.marked beenHere.unconfirmedCount hereNow.count hereNow.summary  \
1           False                         0             0     Nobody here   
2           False                         0             0     Nobody here   
3           False                         0             0     Nobody here   
4           False                         0             0     Nobody here   
5           False                         0             0     Nobody here   

  hereNow.groups  location.crossStreet  venuePage.id  
1             []      Dupont & Spadina      54206610  
2             []                   NaN           NaN  
3             []              at Bloor           NaN  
4             []           Spadina ave           NaN  
5             []         Bloor St West           NaN  

[5 rows x 31 columns]

In [49]:
# filter columns
filtered_columns = ['name',
                    'location.lat', 
                    'location.lng',
                   'location.postalCode']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# clean columns
nearby_venues = nearby_venues[filtered_columns]

nearby_venues.head()

name  location.lat  location.lng location.postalCode
0                   Yoga Flow     43.673844    -79.410134             M5R 1X2
1        The Yoga Back Clinic     43.674701    -79.408514             M5R 1V9
2  Yoga Heritage Healing Arts     43.668750    -79.413173                 NaN
3            Kula Yoga Studio     43.665820    -79.407541             M5S 2M7
4             Urban Edge Yoga     43.667145    -79.403595                 NaN

Let's create a function that iterates through all the neighborhood in our dataframe

In [111]:
def getYogaStudios(names, latitudes, longitudes, radius=5000):
    
    venues_list = []
    
    for name, lat, lng in zip(names, latitudes, longitudes):     
                
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&query=yoga class&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
          
        # make the GET request
        
        results = requests.get(url).json()['response']['groups'][0]['items']
        print(results)                
            
            
        # return only relevant information for each nearby venue
        #if not 
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng']) for v in results])
        
        #Create the dataframe
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude']
    print("Dataframe Created")    
    return(nearby_venues)

In [110]:
query_results = getYogaStudios(names = dfmerge['Neighborhood'],
                                  latitudes = dfmerge['Latitude'],
                                   longitudes = dfmerge['Longitude']
                                  )

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4c18e819d4d9c9284e19f029', 'name': 'LA Fitness', 'contact': {}, 'location': {'address': '1380 Don Mills Road', 'crossStreet': 'Mallard Rd', 'lat': 43.74766522888878, 'lng': -79.34707696065234, 'labeledLatLngs': [{'label': 'display', 'lat': 43.74766522888878, 'lng': -79.34707696065234}], 'distance': 1532, 'postalCode': 'M3B 2X2', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1380 Don Mills Road (Mallard Rd)', 'Toronto ON M3B 2X2', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d176941735', 'name': 'Gym', 'pluralName': 'Gyms', 'shortName': 'Gym', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/gym_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExp

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '50bf6e53d86ce1965377956b', 'name': 'Y Yoga', 'contact': {}, 'location': {'address': '204 - 350 Queens Quay West', 'crossStreet': 'Between Spadina and Rees St.', 'lat': 43.638533613620204, 'lng': -79.38915754933562, 'labeledLatLngs': [{'label': 'display', 'lat': 43.638533613620204, 'lng': -79.38915754933562}], 'distance': 2888, 'postalCode': 'M5V 3A7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['204 - 350 Queens Quay West (Between Spadina and Rees St.)', 'Toronto ON M5V 3A7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '50bf6e53d86ce1965377956b', 'name': 'Y Yoga', 'contact': {}, 'location': {'address': '204 - 350 Queens Quay West', 'crossStreet': 'Between Spadina and Rees St.', 'lat': 43.638533613620204, 'lng': -79.38915754933562, 'labeledLatLngs': [{'label': 'display', 'lat': 43.638533613620204, 'lng': -79.38915754933562}], 'distance': 2888, 'postalCode': 'M5V 3A7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['204 - 350 Queens Quay West (Between Spadina and Rees St.)', 'Toronto ON M5V 3A7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '50bf6e53d86ce1965377956b', 'name': 'Y Yoga', 'contact': {}, 'location': {'address': '204 - 350 Queens Quay West', 'crossStreet': 'Between Spadina and Rees St.', 'lat': 43.638533613620204, 'lng': -79.38915754933562, 'labeledLatLngs': [{'label': 'display', 'lat': 43.638533613620204, 'lng': -79.38915754933562}], 'distance': 2888, 'postalCode': 'M5V 3A7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['204 - 350 Queens Quay West (Between Spadina and Rees St.)', 'Toronto ON M5V 3A7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '50bf6e53d86ce1965377956b', 'name': 'Y Yoga', 'contact': {}, 'location': {'address': '204 - 350 Queens Quay West', 'crossStreet': 'Between Spadina and Rees St.', 'lat': 43.638533613620204, 'lng': -79.38915754933562, 'labeledLatLngs': [{'label': 'display', 'lat': 43.638533613620204, 'lng': -79.38915754933562}], 'distance': 2888, 'postalCode': 'M5V 3A7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['204 - 350 Queens Quay West (Between Spadina and Rees St.)', 'Toronto ON M5V 3A7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0

...

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

In [117]:
query_results.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0          Parkwoods              43.753259              -79.329656   
1          Parkwoods              43.753259              -79.329656   
2  Parkwoods-Donalda              43.753259              -79.329656   
3  Parkwoods-Donalda              43.753259              -79.329656   
4   Victoria Village              43.725882              -79.315572   

             Venue  Venue Latitude  Venue Longitude  
0       LA Fitness       43.747665       -79.347077  
1  Breathe in Yoga       43.777095       -79.348193  
2       LA Fitness       43.747665       -79.347077  
3  Breathe in Yoga       43.777095       -79.348193  
4       LA Fitness       43.747665       -79.347077

In [115]:
yogastudios = query_results.drop_duplicates(subset=['Venue', 'Venue Latitude','Venue Longitude'], keep='first', inplace=False)

In [116]:
yogastudios.shape

(62, 6)

Now that we have all of our data. let's explore the results

### Let's visualize all yoga studios on a map

In [113]:
# create map of Manhattan using latitude and longitude values
map_yoga = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(yogastudios['Venue Latitude'], yogastudios['Venue Longitude'], yogastudios['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_yoga)  
    
map_yoga

In [221]:
countbyneigh = yogastudios.groupby(['Neighborhood']).size().reset_index(name='counts')
countbyneigh = countbyneigh.sort_values(['counts'], ascending = False,ignore_index=True, key=None)
countbyneigh.head()

Neighborhood  counts
0        Regent Park      15
1          Glencairn       6
2  Hillcrest Village       5
3   Islington Avenue       5
4   Woodbine Heights       3

Regent Park is the neighborhood with the most # of yoga studios

#### Let's pull the venues that surrounds a yoga studio

Let's create a function that finds nearby venues

In [165]:
def getNearbyVenues(neighborhood, names, latitudes, longitudes, radius=800):
    
    venues_list = []
    
    for neighb, name, lat, lng in zip(neighborhood, names, latitudes, longitudes):     
                
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
          
        # make the GET request
        
        results = requests.get(url).json()['response']['groups'][0]['items']
        print(results)                
            
            
        # return only relevant information for each nearby venue
        #if not 
        venues_list.append([(
            neighb,
            name, 
            lat, 
            lng,            
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['shortName']) for v in results])
        
        #Create the dataframe
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood','Yoga Place', 
                  'Yoga Place Latitude', 
                  'Yoga Place Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude',
                  'Venue Category']
    print("Dataframe Created")    
    return(nearby_venues)

Let's use our function on the yogastudios dataframe

In [193]:
surrounding_venues = getNearbyVenues(neighborhood = yogastudios['Neighborhood'],
                                     names = yogastudios['Venue'] , 
                                     latitudes = yogastudios['Venue Latitude'], 
                                     longitudes = yogastudios['Venue Longitude'])

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b0aed06f964a520202a23e3', 'name': 'Island Foods', 'contact': {}, 'location': {'address': '1310 Don Mills Rd.', 'lat': 43.745866073988985, 'lng': -79.34603533317939, 'labeledLatLngs': [{'label': 'display', 'lat': 43.745866073988985, 'lng': -79.34603533317939}], 'distance': 217, 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1310 Don Mills Rd.', 'Toronto ON', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d144941735', 'name': 'Caribbean Restaurant', 'pluralName': 'Caribbean Restaurants', 'shortName': 'Caribbean', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/caribbean_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExpiredAt': 0, 'marked': False, 'u

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4e848fbb5c5c9240de8e6a80', 'name': 'The LEGO Store', 'contact': {}, 'location': {'address': '1800 Sheppard Ave E', 'crossStreet': 'at Don Mills Rd', 'lat': 43.77820727238842, 'lng': -79.34348299621146, 'labeledLatLngs': [{'label': 'display', 'lat': 43.77820727238842, 'lng': -79.34348299621146}], 'distance': 398, 'postalCode': 'M2J 5A7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1800 Sheppard Ave E (at Don Mills Rd)', 'Toronto ON M2J 5A7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d1f3941735', 'name': 'Toy / Game Store', 'pluralName': 'Toy / Game Stores', 'shortName': 'Toys & Games', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/toys_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount'

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '5b56812a4420d8002c58cefa', 'name': 'Costco', 'contact': {}, 'location': {'address': '46-42 Overlea Blvd', 'lat': 43.70705091308799, 'lng': -79.3480933503406, 'labeledLatLngs': [{'label': 'display', 'lat': 43.70705091308799, 'lng': -79.3480933503406}], 'distance': 323, 'postalCode': 'M4H 1B6', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['46-42 Overlea Blvd', 'Toronto ON M4H 1B6', 'Canada']}, 'categories': [{'id': '52e816a6bcbc57f1066b7a54', 'name': 'Warehouse Store', 'pluralName': 'Warehouse Stores', 'shortName': 'Warehouse Store', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/default_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExpiredAt': 0, '

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b618500f964a52090162ae3', 'name': 'HTO Park', 'contact': {}, 'location': {'address': "Queen's Quay", 'crossStreet': 'at Rees St.', 'lat': 43.63794857171933, 'lng': -79.38781965601113, 'labeledLatLngs': [{'label': 'display', 'lat': 43.63794857171933, 'lng': -79.38781965601113}], 'distance': 125, 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ["Queen's Quay (at Rees St.)", 'Toronto ON', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d163941735', 'name': 'Park', 'pluralName': 'Parks', 'shortName': 'Park', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/park_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExpiredAt': 0, 'marked': False, 'unconfi

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '51755dc7498ece19b7261641', 'name': 'Banh Mi Boys', 'contact': {}, 'location': {'address': '399 Yonge St.', 'crossStreet': 'Gerrard St.', 'lat': 43.659292, 'lng': -79.381949, 'labeledLatLngs': [{'label': 'display', 'lat': 43.659292, 'lng': -79.381949}], 'distance': 280, 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['399 Yonge St. (Gerrard St.)', 'Toronto ON', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d1c5941735', 'name': 'Sandwich Place', 'pluralName': 'Sandwich Places', 'shortName': 'Sandwiches', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/deli_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExpiredAt': 0, 'marked': False, 'unconfirmedCount'

...

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b6efbf8f964a520c1d42ce3', 'name': 'Concord Food Centre', 'contact': {}, 'location': {'address': '1438 Centre Street', 'crossStreet': 'Dufferin', 'lat': 43.80647581743824, 'lng': -79.47271404370676, 'labeledLatLngs': [{'label': 'display', 'lat': 43.80647581743824, 'lng': -79.47271404370676}], 'distance': 90, 'postalCode': 'L4J 3N1', 'cc': 'CA', 'city': 'Thornhill', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1438 Centre Street (Dufferin)', 'Thornhill ON L4J 3N1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d118951735', 'name': 'Grocery Store', 'pluralName': 'Grocery Stores', 'shortName': 'Grocery Store', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_grocery_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '551486ff498ee91ac6d40f43', 'name': 'Starbucks', 'contact': {}, 'location': {'address': '150 Park Lawn Rd, Unit A', 'crossStreet': 'The Queensway', 'lat': 43.627931, 'lng': -79.489286, 'labeledLatLngs': [{'label': 'display', 'lat': 43.627931, 'lng': -79.489286}], 'distance': 390, 'postalCode': 'M8Y 3H8', 'cc': 'CA', 'neighborhood': 'Stonegate - Queensway', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['150 Park Lawn Rd, Unit A (The Queensway)', 'Toronto ON M8Y 3H8', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d1e0931735', 'name': 'Coffee Shop', 'pluralName': 'Coffee Shops', 'shortName': 'Coffee Shop', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/coffeeshop_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCo

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '54f778ee498ed2f9927ca692', 'name': "Longo's", 'contact': {}, 'location': {'address': '1125 North Service Rd', 'crossStreet': 'Stansfield', 'lat': 43.59241587967815, 'lng': -79.57446335230044, 'labeledLatLngs': [{'label': 'display', 'lat': 43.59241587967815, 'lng': -79.57446335230044}], 'distance': 136, 'postalCode': 'L4Y 1A6', 'cc': 'CA', 'city': 'Mississauga', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1125 North Service Rd (Stansfield)', 'Mississauga ON L4Y 1A6', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d118951735', 'name': 'Grocery Store', 'pluralName': 'Grocery Stores', 'shortName': 'Grocery Store', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_grocery_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount':

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '54f778ee498ed2f9927ca692', 'name': "Longo's", 'contact': {}, 'location': {'address': '1125 North Service Rd', 'crossStreet': 'Stansfield', 'lat': 43.59241587967815, 'lng': -79.57446335230044, 'labeledLatLngs': [{'label': 'display', 'lat': 43.59241587967815, 'lng': -79.57446335230044}], 'distance': 155, 'postalCode': 'L4Y 1A6', 'cc': 'CA', 'city': 'Mississauga', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1125 North Service Rd (Stansfield)', 'Mississauga ON L4Y 1A6', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d118951735', 'name': 'Grocery Store', 'pluralName': 'Grocery Stores', 'shortName': 'Grocery Store', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_grocery_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount':

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '5a2d984cc6666601b62748f4', 'name': 'Air Canada Signature Suite', 'contact': {}, 'location': {'address': 'Terminal 1, Concourse E', 'crossStreet': 'Toronto Pearson International Airport', 'lat': 43.676704557733416, 'lng': -79.61103533569258, 'labeledLatLngs': [{'label': 'display', 'lat': 43.676704557733416, 'lng': -79.61103533569258}], 'distance': 91, 'postalCode': 'L5P', 'cc': 'CA', 'city': 'Mississauga', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['Terminal 1, Concourse E (Toronto Pearson International Airport)', 'Mississauga ON L5P', 'Canada']}, 'categories': [{'id': '4eb1bc533b7b2c5b1d4306cb', 'name': 'Airport Lounge', 'pluralName': 'Airport Lounges', 'shortName': 'Lounge', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/nightlife/default_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'t

In [194]:
surrounding_venues.head(12)

Neighborhood  Yoga Place  Yoga Place Latitude  Yoga Place Longitude  \
0     Parkwoods  LA Fitness            43.747665            -79.347077   
1     Parkwoods  LA Fitness            43.747665            -79.347077   
2     Parkwoods  LA Fitness            43.747665            -79.347077   
3     Parkwoods  LA Fitness            43.747665            -79.347077   
4     Parkwoods  LA Fitness            43.747665            -79.347077   
5     Parkwoods  LA Fitness            43.747665            -79.347077   
6     Parkwoods  LA Fitness            43.747665            -79.347077   
7     Parkwoods  LA Fitness            43.747665            -79.347077   
8     Parkwoods  LA Fitness            43.747665            -79.347077   
9     Parkwoods  LA Fitness            43.747665            -79.347077   
10    Parkwoods  LA Fitness            43.747665            -79.347077   
11    Parkwoods  LA Fitness            43.747665            -79.347077   

                                    Venue  Venue Latitude  Venue Longitude  \
0                            Island Foods       43.745866       -79.346035   
1                              LA Fitness       43.747665       -79.347077   
2                           Baretto Caffé       43.744456       -79.346460   
3                    Galleria Supermarket       43.753520       -79.349518   
4   Matsuda Japanese Cuisine & Teppanyaki       43.745494       -79.345821   
5             Donalda Golf & Country Club       43.752816       -79.342741   
6                             Gonoe Sushi       43.745737       -79.345991   
7                         TD Canada Trust       43.753253       -79.347851   
8                               Five Guys       43.754514       -79.350004   
9                  Dragon Pearl Buffet 龍珠       43.753693       -79.349730   
10              the REALTOR® Store @ TREB       43.749428       -79.347339   
11                          National Post       43.752404       -79.347897   

     Venue Category  
0         Caribbean  
1               Gym  
2              Café  
3       Supermarket  
4          Japanese  
5       Golf Course  
6          Japanese  
7              Bank  
8           Burgers  
9             Asian  
10  Office Supplies  
11           Office

In [196]:
surrounding_venues = surrounding_venues.drop(surrounding_venues[(surrounding_venues["Venue Category"] == 'Yoga Studio')].index)

In [197]:
surrounding_venues.head()

Neighborhood  Yoga Place  Yoga Place Latitude  Yoga Place Longitude  \
0    Parkwoods  LA Fitness            43.747665            -79.347077   
1    Parkwoods  LA Fitness            43.747665            -79.347077   
2    Parkwoods  LA Fitness            43.747665            -79.347077   
3    Parkwoods  LA Fitness            43.747665            -79.347077   
4    Parkwoods  LA Fitness            43.747665            -79.347077   

                                   Venue  Venue Latitude  Venue Longitude  \
0                           Island Foods       43.745866       -79.346035   
1                             LA Fitness       43.747665       -79.347077   
2                          Baretto Caffé       43.744456       -79.346460   
3                   Galleria Supermarket       43.753520       -79.349518   
4  Matsuda Japanese Cuisine & Teppanyaki       43.745494       -79.345821   

  Venue Category  
0      Caribbean  
1            Gym  
2           Café  
3    Supermarket  
4       Japanese

In [217]:
around_yoga = surrounding_venues.groupby(['Venue Category']).size().reset_index(name='Category Count')
around_yoga.head()

Venue Category  Category Count
0      Accessories               1
1           Afghan               1
2          Airport               1
3  Airport Service               1
4         American               7

Let's sort the data based on the Category Count from highest to lowest

In [218]:
sorted_aroundyoga = around_yoga.sort_values('Category Count',ascending=False, ignore_index=True, key=None)

<h2 style="color:blue;">3. <u>Methodology</u></h2>

Based on the data, it appears that there might be a correlation between coffee shops and yoga studios.

<h2 style="color:blue;">4. <u>Results</u></h2
    

### Based on the data, the Regent Park neighborhood has the highest # of yoga studios.

In [222]:
countbyneigh.head()

Neighborhood  counts
0        Regent Park      15
1          Glencairn       6
2  Hillcrest Village       5
3   Islington Avenue       5
4   Woodbine Heights       3

### Many Yoga Studios are surrounded by Coffee Shops followed by Italian Restaurants

In [220]:
sorted_aroundyoga.head(5)

Venue Category  Category Count
0    Coffee Shop              80
1        Italian              54
2           Café              42
3     Restaurant              35
4  Grocery Store              33

<h2 style="color:blue;">5. <u>Discussion</u></h2>

<h2 style="color:blue;">6. <u>Conclusion</u><h2>